# Imports 

In [100]:
import pandas as pd
import os
import numpy as np
import scipy as sp
import re
from sklearn.feature_extraction import stop_words as stop
pd.set_option('display.max_colwidth', -1)
pd.set_option('display.max_rows', 10)

# Functions

In [101]:
# used to mostly make the accuracy scores more readable
def make_percent(num):
    return '%.2f'%(num * 100) + '%'

# go through 'columns' of 'df' and replace parts of text based on 'regx' with "".
# used here to remove syntax from each headline in the dataframe
def df_regx_replace(df, columns, regx):
    for col in columns:
        df[col] = df[col].replace(to_replace = regx, value = "", regex = True)
        df[col] = df[col].str.lower()
    return df
        
# go through each column and tokenize/un-stop-word it. 
# used to begin the proccess of text normalization
def df_text_analyzer(df, columns, analyzer):
    for col in columns:
        column = df[col].copy()
        for index, val in column.iteritems():
            column.loc[index] = analyzer(val)
        df[col] = column
    return df

# remove rows that contain nan values
# used to remove 3 rows from this specific data set
def df_text_remove_nan(df):
    for row_index, row in df.iterrows():
        has_nan = False
        for index, val in row.iteritems():
            if(pd.isnull(val)):
                has_nan = True
        if (has_nan):
            print("removed row: " + str(row_index))
            df = df.drop(axis = 0, labels = row_index)
    return df

# create a single array of all the tokens that occurr in the data set.
def df_text_single_array(df, columns):
    element_index = 0;
    for col in columns:
        column = df[col].copy()
        col_num = 0
        for row_index, row_val in column.iteritems():
            for element in row_val:
                element_index = element_index + 1
    array = np.empty(shape = element_index, dtype = "S30")
    element_index = 0
    for col in columns:
        column = df[col].copy()
        for row_index, row_val in column.iteritems():
            for element in row_val:
                array[element_index] = element
                element_index = element_index + 1
    return array

# may not be needed, used to iterate through all cells in a df and transforming with
# tfidf transform function. Was having memory? issues.
def df_tfidf_transform(df, columns, tfidf):
    for col in columns:
        column = df[col].copy()
        for row_index, row_val in column.iteritems():
#             print(tfidf.transform(row_val))
            columns.loc[row_index] = tfidf.transform(row_val)
            print(columns.iloc[row_index])
#         df[col] = column
    return df

# append all the columns into one column, used to combine columns for aggregate vectorization.
def df_concat_str_columns(df, columns):
    concat_columns = df['Top1'].copy()
    for row_index, row_value in df.iterrows():
        single_string = ""
        for col in columns:
            single_string = single_string + " " + df[col].loc[row_index]
        concat_columns[row_index] = single_string
    return concat_columns

# Parse the data
Read the data into a dataframe, vectorize the first headline column, and extract the labels column.

## Import data

In [102]:
data_set = pd.read_csv("C:\\Users\\carmi\\OneDrive\\Documents\\Datasets\\stocknews\\Combined_News_DJIA.csv")
df_original = pd.DataFrame(data_set)
df_original

Date  Label  \
0     2008-08-08  0       
1     2008-08-11  1       
2     2008-08-12  0       
3     2008-08-13  0       
4     2008-08-14  1       
...          ... ..       
1984  2016-06-27  0       
1985  2016-06-28  1       
1986  2016-06-29  1       
1987  2016-06-30  1       
1988  2016-07-01  1       

                                                                                                                                                                                                         Top1  \
0     b"Georgia 'downs two Russian warplanes' as countries move to brink of war"                                                                                                                                
1     b'Why wont America and Nato help us? If they wont help us now, why did we help them in Iraq?'                                                                                                             
2     b'Remember that adorable 9-year-old who sang at the opening ceremonies? That was fake, too.'                                                                                                              
3     b' U.S. refuses Israel weapons to attack Iran: report'                                                                                                                                                    
4     b'All the experts admit that we should legalise drugs '                                                                                                                                                   
...                                                       ...                                                                                                                                                   
1984  Barclays and RBS shares suspended from trading after tanking more than 8%                                                                                                                                 
1985  2,500 Scientists To Australia: If You Want To Save The Great Barrier Reef, Stop Supporting Coal                                                                                                           
1986  Explosion At Airport In Istanbul                                                                                                                                                                          
1987  Jamaica proposes marijuana dispensers for tourists at airports following legalisation: The kiosks and desks would give people a license to purchase up to 2 ounces of the drug to use during their stay   
1988  A 117-year-old woman in Mexico City finally received her birth certificate, and died a few hours later. Trinidad Alvarez Lira had waited years for proof that she had been born in 1898.                  

                                                                                                                                                                                                   Top2  \
0     b'BREAKING: Musharraf to be impeached.'                                                                                                                                                             
1     b'Bush puts foot down on Georgian conflict'                                                                                                                                                         
2     b"Russia 'ends Georgia operation'"                                                                                                                                                                  
3     b"When the president ordered to attack Tskhinvali [the capital of South Ossetia], we knew then we were doomed. How come he didn't realize that?"                                                    
4     b'War in South Osetia - 89 pictures made by a Russian soldier.'                                                                                              

Import the combined dataset, and place it in a dataframe. This dataset has labels with values 0 - indicating the DJIA went down, and 1 - indicating the DJIA went up or stayed the same. The next 27 columns are the top 27 headlines for a given date in ascending order.

## Clean data
There are a few things we need to do in order to make this data easier to work with. Thankfully, there are no missing values. However, we will want to do some basic text processing in order to get rid of things like stop words, syntax, and more easily vectorize the headlines.

In [103]:
columns = df.iloc[:, 2:]
regx = "[/\-_\+=\*,\.\"\'()!\?@#$%\^;:\[\]]|^b[\'\"]*"
df_no_syntax = df_regx_replace(df_original, columns, regx)
df_no_syntax

Date  Label  \
0     2008-08-08  0       
1     2008-08-11  1       
2     2008-08-12  0       
3     2008-08-13  0       
4     2008-08-14  1       
...          ... ..       
1984  2016-06-27  0       
1985  2016-06-28  1       
1986  2016-06-29  1       
1987  2016-06-30  1       
1988  2016-07-01  1       

                                                                                                                                                                                                        Top1  \
0     georgia downs two russian warplanes as countries move to brink of war                                                                                                                                    
1     why wont america and nato help us if they wont help us now why did we help them in iraq                                                                                                                  
2     remember that adorable 9yearold who sang at the opening ceremonies that was fake too                                                                                                                     
3      us refuses israel weapons to attack iran report                                                                                                                                                         
4     all the experts admit that we should legalise drugs                                                                                                                                                      
...                                                    ...                                                                                                                                                     
1984  barclays and rbs shares suspended from trading after tanking more than 8                                                                                                                                 
1985  2500 scientists to australia if you want to save the great barrier reef stop supporting coal                                                                                                             
1986  explosion at airport in istanbul                                                                                                                                                                         
1987  jamaica proposes marijuana dispensers for tourists at airports following legalisation the kiosks and desks would give people a license to purchase up to 2 ounces of the drug to use during their stay   
1988  a 117yearold woman in mexico city finally received her birth certificate and died a few hours later trinidad alvarez lira had waited years for proof that she had been born in 1898                      

                                                                                                                                                                                                   Top2  \
0     b'BREAKING: Musharraf to be impeached.'                                                                                                                                                             
1     b'Bush puts foot down on Georgian conflict'                                                                                                                                                         
2     b"Russia 'ends Georgia operation'"                                                                                                                                                                  
3     b"When the president ordered to attack Tskhinvali [the capital of South Ossetia], we knew then we were doomed. How come he didn't realize that?"                                                    
4     b'War in South Osetia - 89 pictures made by a Russian soldier.'                                                                                                          

Removed all puncation/syntax, and lowercased each headline for easier parasing.

In [104]:
df_no_nan = df_text_remove_nan(df_no_syntax)
df_no_nan

removed row: 277
removed row: 348
removed row: 681


Date  Label  \
0     2008-08-08  0       
1     2008-08-11  1       
2     2008-08-12  0       
3     2008-08-13  0       
4     2008-08-14  1       
...          ... ..       
1984  2016-06-27  0       
1985  2016-06-28  1       
1986  2016-06-29  1       
1987  2016-06-30  1       
1988  2016-07-01  1       

                                                                                                                                                                                                        Top1  \
0     georgia downs two russian warplanes as countries move to brink of war                                                                                                                                    
1     why wont america and nato help us if they wont help us now why did we help them in iraq                                                                                                                  
2     remember that adorable 9yearold who sang at the opening ceremonies that was fake too                                                                                                                     
3      us refuses israel weapons to attack iran report                                                                                                                                                         
4     all the experts admit that we should legalise drugs                                                                                                                                                      
...                                                    ...                                                                                                                                                     
1984  barclays and rbs shares suspended from trading after tanking more than 8                                                                                                                                 
1985  2500 scientists to australia if you want to save the great barrier reef stop supporting coal                                                                                                             
1986  explosion at airport in istanbul                                                                                                                                                                         
1987  jamaica proposes marijuana dispensers for tourists at airports following legalisation the kiosks and desks would give people a license to purchase up to 2 ounces of the drug to use during their stay   
1988  a 117yearold woman in mexico city finally received her birth certificate and died a few hours later trinidad alvarez lira had waited years for proof that she had been born in 1898                      

                                                                                                                                                                                                   Top2  \
0     b'BREAKING: Musharraf to be impeached.'                                                                                                                                                             
1     b'Bush puts foot down on Georgian conflict'                                                                                                                                                         
2     b"Russia 'ends Georgia operation'"                                                                                                                                                                  
3     b"When the president ordered to attack Tskhinvali [the capital of South Ossetia], we knew then we were doomed. How come he didn't realize that?"                                                    
4     b'War in South Osetia - 89 pictures made by a Russian soldier.'                                                                                                          

Remove any rows that contain nan values in the columns.

# Baseline accuracy 
To quickly get a baseline accuracy, combining the columns seems to be the simplest way to get a vectorized data set for classification input. We will do more nuanced vectorization and classification after getting a baseline for this dataset.

## Combine columns

In [105]:
df = df_no_nan
columns = df.iloc[:, 2:]
concat_column = df_concat_str_columns(df, columns)
concat_column = pd.DataFrame(concat_column)
concat_column

Top1
0      georgia downs two russian warplanes as countries move to brink of war b'BREAKING: Musharraf to be impeached.' b'Russia Today: Columns of troops roll into South Ossetia; footage from fighting (YouTube)' b'Russian tanks are moving towards the capital of South Ossetia, which has reportedly been completely destroyed by Georgian artillery fire' b"Afghan children raped with 'impunity,' U.N. official says - this is sick, a three year old was raped and they do nothing" b'150 Russian tanks have entered South Ossetia whilst Georgia shoots down two Russian jets.' b"Breaking: Georgia invades South Ossetia, Russia warned it would intervene on SO's side" b"The 'enemy combatent' trials are nothing but a sham: Salim Haman has been sentenced to 5 1/2 years, but will be kept longer anyway just because they feel like it." b'Georgian troops retreat from S. Osettain capital, presumably leaving several hundred people killed. [VIDEO]' b'Did the U.S. Prep Georgia for War with Russia?' b'Rice Gives Green Light for Israel to Attack Iran: Says U.S. has no veto over Israeli military ops' b'Announcing:Class Action Lawsuit on Behalf of American Public Against the FBI' b"So---Russia and Georgia are at war and the NYT's top story is opening ceremonies of the Olympics?  What a fucking disgrace and yet further proof of the decline of journalism." b"China tells Bush to stay out of other countries' affairs" b'Did World War III start today?' b'Georgia Invades South Ossetia - if Russia gets involved, will NATO absorb Georgia and unleash a full scale war?' b'Al-Qaeda Faces Islamist Backlash' b'Condoleezza Rice: "The US would not act to prevent an Israeli strike on Iran." Israeli Defense Minister Ehud Barak: "Israel is prepared for uncompromising victory in the case of military hostilities."' b'This is a busy day:  The European Union has approved new sanctions against Iran in protest at its nuclear programme.' b"Georgia will withdraw 1,000 soldiers from Iraq to help fight off Russian forces in Georgia's breakaway region of South Ossetia" b'Why the Pentagon Thinks Attacking Iran is a Bad Idea - US News &amp; World Report' b'Caucasus in crisis: Georgia invades South Ossetia' b'Indian shoe manufactory  - And again in a series of "you do not like your work?"' b'Visitors Suffering from Mental Illnesses Banned from Olympics' b"No Help for Mexico's Kidnapping Surge"                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                
1      why wont america and nato help us if they wont help us now why did we help them in iraq b'Bush puts foot down on Georgian conflict' b"Jewish Georgian minister: Thanks to Israeli training, we're fending off Russia " b'Georgian army flees in disarray as Russians advance - Gori abandoned to Russia without a shot fired' b"Olympic opening ceremony fireworks 'faked'" b'What were the Mossad with fraudulent New Zealand Passports doing in Iraq?' b'Russia angered by Israeli military sale to Georgia' b'An American citizen living in S.Ossetia blames U.S. and Georgian leaders for the genocide of innocent people' b'Welcome To World War IV! Now In High Definition!' b"Georgia's move, a mistake of monumental proportions " b'Russia presses deeper 

Concatenate all the headlines into one corpus to be vectorized in a tdidf/word count vectorizer

In [79]:
df = df.drop(labels = columns.columns, axis = 1)
# df = df.merge(concat_column)
df = pd.concat([df, concat_column], axis = 1)
df

Date  Label  \
0     2008-08-08  0       
1     2008-08-11  1       
2     2008-08-12  0       
3     2008-08-13  0       
4     2008-08-14  1       
...          ... ..       
1984  2016-06-27  0       
1985  2016-06-28  1       
1986  2016-06-29  1       
1987  2016-06-30  1       
1988  2016-07-01  1       

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 Top1  
0      georgia downs two russian warplanes as countries move to brink of war breaking musharraf to be impeached russia today columns of troops roll into south ossetia footage from fighting youtube russian tanks are moving towards the capital of south ossetia which has reportedly been completely destroyed by georgian artillery fire afghan children raped with impunity un official says  this is sick a three year old was raped and they do nothing 150 russian tanks have entered south ossetia whilst georgia shoo

Remove redundant, non-combined columns and append the new concatenated column onto the existing dataframe with labels.

## Form a baseline 

In [86]:
from sklearn.feature_extraction.text import TfidfVectorizer
sw = stop.ENGLISH_STOP_WORDS
tfidf = TfidfVectorizer(stop_words = sw)
tfidf.fit(df['Top1'])
print(tfidf.get_feature_names()[0:1000])

['000', '0001', '001', '003', '004', '005', '006', '007', '0077', '00s', '01', '011', '014', '014ckwh', '017', '02', '0200', '021hour', '022', '0220', '0221', '025', '03', '030', '035017', '04', '05', '050', '05eurgb', '06', '060', '062', '068as', '07', '07232014', '075', '07baku1268', '07pc', '08', '089m', '08baku671', '09', '0900', '0930', '0935', '10', '100', '1000', '10000', '100000', '1000000', '1000000000', '100000man', '100000person', '100000th', '10000s', '10000strong', '10000yearold', '10001500', '1000km', '1000megawatt', '1000per', '1000s', '1000strong', '1000x', '1000year', '1000yearold', '100200', '1004', '1004am', '1006', '100abarrel', '100apack', '100billion', '100bn', '100day', '100ds', '100fold', '100foot', '100ft', '100k', '100km', '100m', '100mil', '100million', '100mstretch', '100mw', '100page', '100s', '100th', '100x', '100year', '100yearold', '101', '1011', '1012', '1017', '101st', '102', '1020', '102000', '1021', '10262010', '102day', '102yearold', '103', '1030', 

Create a dictionary in a tfidf vectorizer given our concatenated dataset.

In [99]:
features = tfidf.transform(df['Top1'])
data_labels = df['Label']
display(features)
print(features)

<1986x39900 sparse matrix of type '<class 'numpy.float64'>'
	with 489780 stored elements in Compressed Sparse Row format>

  (0, 39697)	0.04792113397841143
  (0, 39586)	0.018635470668102998
  (0, 39576)	0.02309480578615759
  (0, 39317)	0.03510663510162514
  (0, 39295)	0.03222955083293025
  (0, 39198)	0.052627215370409826
  (0, 38962)	0.07472527781990451
  (0, 38644)	0.05458685467845757
  (0, 38632)	0.03848278340226787
  (0, 38591)	0.09580465919607202
  (0, 38346)	0.05874965900421731
  (0, 38220)	0.028760672420553638
  (0, 38214)	0.04589661170480536
  (0, 38159)	0.0641100318305066
  (0, 37476)	0.07190063735605241
  (0, 37430)	0.03528136571540746
  (0, 37203)	0.08424845497195356
  (0, 36718)	0.057575186629517626
  (0, 36629)	0.055135230165267744
  (0, 36160)	0.0639523086984654
  (0, 35872)	0.05955281974015128
  (0, 35600)	0.035923795876247486
  (0, 35374)	0.09332647229079422
  (0, 34955)	0.05458685467845757
  (0, 34709)	0.04748600345927687
  :	:
  (1985, 3536)	0.09229817581704898
  (1985, 3108)	0.0404703132373173
  (1985, 3009)	0.03580320373466395
  (1985, 2796)	0.06189488586264328
  (1985, 2761)	0.035896283

We have converted the *whole* column of concatenated headlines into a single sparse matrix using the tfidf transformer built on the dictionary created earlier. At this point, I'm not sure if I should have created a sparse matrix for each row, or use the above method instead. So, for this baseline, I will perform both.

In [6]:
analyzer = tfidf.build_analyzer()
columns = df.iloc[:, 2:]
df = df_text_analyzer(df, columns, analyzer)
df

Date  Label  \
0     2008-08-08  0       
1     2008-08-11  1       
2     2008-08-12  0       
3     2008-08-13  0       
4     2008-08-14  1       
...          ... ..       
1984  2016-06-27  0       
1985  2016-06-28  1       
1986  2016-06-29  1       
1987  2016-06-30  1       
1988  2016-07-01  1       

                                                                                                                                                            Top1  \
0     [georgia, downs, russian, warplanes, countries, brink, war]                                                                                                  
1     [wont, america, nato, help, wont, help, did, help, iraq]                                                                                                     
2     [remember, adorable, 9yearold, sang, opening, ceremonies, fake]                                                                                              
3     [refuses, israel, weapons, attack, iran, report]                                                                                                             
4     [experts, admit, legalise, drugs]                                                                                                                            
...                                 ...                                                                                                                            
1984  [barclays, rbs, shares, suspended, trading, tanking]                                                                                                         
1985  [2500, scientists, australia, want, save, great, barrier, reef, stop, supporting, coal]                                                                      
1986  [explosion, airport, istanbul]                                                                                                                               
1987  [jamaica, proposes, marijuana, dispensers, tourists, airports, following, legalisation, kiosks, desks, people, license, purchase, ounces, drug, use, stay]   
1988  [117yearold, woman, mexico, city, finally, received, birth, certificate, died, hours, later, trinidad, alvarez, lira, waited, years, proof, born, 1898]      

                                                                                                                                                       Top2  \
0     [breaking, musharraf, impeached]                                                                                                                        
1     [bush, puts, foot, georgian, conflict]                                                                                                                  
2     [russia, ends, georgia, operation]                                                                                                                      
3     [president, ordered, attack, tskhinvali, capital, south, ossetia, knew, doomed, come, didnt, realize]                                                   
4     [war, south, osetia, 89, pictures, russian, soldier]                                                                                                    
...                                                    ...                                                                                                    
1984  [pope, says, church, ask, forgiveness, gays, past, treatment]                                                                                           
1985  [personal, details, 112000, french, police, officers, uploaded, google, drive, security, breach, just, fortnight, officers, murdered, home, jihadist]   
1986  [yemeni, president, terrorism, offspring, wahhabism, al, saud, regime]                                                                                  
1987  [stephen, hawking, says, pollution, stupidity, biggest, threats, mankind, certainly, greedy, stupid, treatment, environmen

Tokenize and remove stop words for each headline for easier processing in classifiers.

In [7]:
single_array = df_text_single_array(df, columns)
print(single_array[0:1000])

[b'georgia' b'downs' b'russian' b'warplanes' b'countries' b'brink' b'war'
 b'wont' b'america' b'nato' b'help' b'wont' b'help' b'did' b'help' b'iraq'
 b'remember' b'adorable' b'9yearold' b'sang' b'opening' b'ceremonies'
 b'fake' b'refuses' b'israel' b'weapons' b'attack' b'iran' b'report'
 b'experts' b'admit' b'legalise' b'drugs' b'mom' b'missing' b'gay' b'man'
 b'bad' b'hes' b'21yearold' b'cheerleader' b'theyd' b'looking' b'afghan'
 b'prison' b'majority' b'female' b'prisoners' b'serving' b'20year'
 b'sentences' b'victims' b'rape' b'man' b'arrested' b'locked' b'hours'
 b'taking' b'photo' b'police' b'van' b'ignoring' b'entry' b'sign'
 b'elderly' b'chinese' b'women' b'sentenced' b'year' b'reeducation'
 b'labor' b'sought' b'permit' b'demonstrate' b'official' b'olympic'
 b'protest' b'area' b'british' b'resident' b'held' b'guantanamo' b'bay'
 b'wins' b'legal' b'battle' b'force' b'foreign' b'office' b'reveal'
 b'torture' b'evidence' b'syria' b'says' b'ready' b'russian' b'missile'
 b'soil' b'co

Create a single array of all tokens to build a dictionary from

In [8]:
tfidf.fit(single_array)
print(len(tfidf.get_feature_names()))
print(tfidf.get_feature_names()[0:1000])

39900
['000', '0001', '001', '003', '004', '005', '006', '007', '0077', '00s', '01', '011', '014', '014ckwh', '017', '02', '0200', '021hour', '022', '0220', '0221', '025', '03', '030', '035017', '04', '05', '050', '05eurgb', '06', '060', '062', '068as', '07', '07232014', '075', '07baku1268', '07pc', '08', '089m', '08baku671', '09', '0900', '0930', '0935', '10', '100', '1000', '10000', '100000', '1000000', '1000000000', '100000man', '100000person', '100000th', '10000s', '10000strong', '10000yearold', '10001500', '1000km', '1000megawatt', '1000per', '1000s', '1000strong', '1000x', '1000year', '1000yearold', '100200', '1004', '1004am', '1006', '100abarrel', '100apack', '100billion', '100bn', '100day', '100ds', '100fold', '100foot', '100ft', '100k', '100km', '100m', '100mil', '100million', '100mstretch', '100mw', '100page', '100s', '100th', '100x', '100year', '100yearold', '101', '1011', '1012', '1017', '101st', '102', '1020', '102000', '1021', '10262010', '102day', '102yearold', '103', '1

Create a dictionary for a tfidf vectorizer.

In [10]:
columns = df.iloc[:, 2:]
df = df_tfidf_transform(df, columns, tfidf)
# df


Top1       (0, 15944)\t1.0\n  (1, 12175)\t1.0\n  (2, 31184)\t1.0\n  (3, 38644)\t1.0\n  (4, 9834)\t1.0\n  (5, 6850)\t1.0\n  (6, 38591)\t1.0
Top2       (0, 15944)\t1.0\n  (1, 12175)\t1.0\n  (2, 31184)\t1.0\n  (3, 38644)\t1.0\n  (4, 9834)\t1.0\n  (5, 6850)\t1.0\n  (6, 38591)\t1.0
Top3       (0, 15944)\t1.0\n  (1, 12175)\t1.0\n  (2, 31184)\t1.0\n  (3, 38644)\t1.0\n  (4, 9834)\t1.0\n  (5, 6850)\t1.0\n  (6, 38591)\t1.0
Top4       (0, 15944)\t1.0\n  (1, 12175)\t1.0\n  (2, 31184)\t1.0\n  (3, 38644)\t1.0\n  (4, 9834)\t1.0\n  (5, 6850)\t1.0\n  (6, 38591)\t1.0
Top5       (0, 15944)\t1.0\n  (1, 12175)\t1.0\n  (2, 31184)\t1.0\n  (3, 38644)\t1.0\n  (4, 9834)\t1.0\n  (5, 6850)\t1.0\n  (6, 38591)\t1.0
                                                                       ...                                                                
Top21      (0, 15944)\t1.0\n  (1, 12175)\t1.0\n  (2, 31184)\t1.0\n  (3, 38644)\t1.0\n  (4, 9834)\t1.0\n  (5, 6850)\t1.0\n  (6, 38591)\t1.0
Top22      (0, 15944)\t1.0\

Top1       (0, 21793)\t1.0\n  (1, 39317)\t1.0\n  (2, 35765)\t1.0\n  (3, 28290)\t1.0\n  (4, 23263)\t1.0\n  (5, 31401)\t1.0\n  (6, 34799)\t1.0\n  (7, 15080)\t1.0\n  (8, 30349)\t1.0\n  (9, 9866)\t1.0\n  (10, 31318)\t1.0\n  (11, 38294)\t1.0\n  (12, 9426)\t1.0\n  (13, 17965)\t1.0\n  (14, 9610)\t1.0\n  (15, 32237)\t1.0
Top2       (0, 21793)\t1.0\n  (1, 39317)\t1.0\n  (2, 35765)\t1.0\n  (3, 28290)\t1.0\n  (4, 23263)\t1.0\n  (5, 31401)\t1.0\n  (6, 34799)\t1.0\n  (7, 15080)\t1.0\n  (8, 30349)\t1.0\n  (9, 9866)\t1.0\n  (10, 31318)\t1.0\n  (11, 38294)\t1.0\n  (12, 9426)\t1.0\n  (13, 17965)\t1.0\n  (14, 9610)\t1.0\n  (15, 32237)\t1.0
Top3       (0, 21793)\t1.0\n  (1, 39317)\t1.0\n  (2, 35765)\t1.0\n  (3, 28290)\t1.0\n  (4, 23263)\t1.0\n  (5, 31401)\t1.0\n  (6, 34799)\t1.0\n  (7, 15080)\t1.0\n  (8, 30349)\t1.0\n  (9, 9866)\t1.0\n  (10, 31318)\t1.0\n  (11, 38294)\t1.0\n  (12, 9426)\t1.0\n  (13, 17965)\t1.0\n  (14, 9610)\t1.0\n  (15, 32237)\t1.0
Top4       (0, 21793)\t1.0\n  (1, 39317)\t1.0\n  (2, 35

Top1       (0, 22221)\t1.0\n  (1, 27643)\t1.0
Top2       (0, 22221)\t1.0\n  (1, 27643)\t1.0
Top3       (0, 22221)\t1.0\n  (1, 27643)\t1.0
Top4       (0, 22221)\t1.0\n  (1, 27643)\t1.0
Top5       (0, 22221)\t1.0\n  (1, 27643)\t1.0
                         ...                 
Top21      (0, 22221)\t1.0\n  (1, 27643)\t1.0
Top22      (0, 22221)\t1.0\n  (1, 27643)\t1.0
Top23      (0, 22221)\t1.0\n  (1, 27643)\t1.0
Top24      (0, 22221)\t1.0\n  (1, 27643)\t1.0
Top25      (0, 22221)\t1.0\n  (1, 27643)\t1.0
Name: 49, Length: 25, dtype: object
Top1       (0, 8801)\t1.0\n  (1, 10633)\t1.0\n  (2, 5161)\t1.0\n  (3, 26703)\t1.0\n  (4, 17998)\t1.0\n  (5, 28337)\t1.0\n  (6, 39872)\t1.0
Top2       (0, 8801)\t1.0\n  (1, 10633)\t1.0\n  (2, 5161)\t1.0\n  (3, 26703)\t1.0\n  (4, 17998)\t1.0\n  (5, 28337)\t1.0\n  (6, 39872)\t1.0
Top3       (0, 8801)\t1.0\n  (1, 10633)\t1.0\n  (2, 5161)\t1.0\n  (3, 26703)\t1.0\n  (4, 17998)\t1.0\n  (5, 28337)\t1.0\n  (6, 39872)\t1.0
Top4       (0, 8801)\t1.0\n  (1, 10633)\t

Top1       (0, 7165)\t1.0\n  (1, 18347)\t1.0\n  (2, 39317)\t1.0\n  (3, 21040)\t1.0\n  (4, 15613)\t1.0\n  (5, 22769)\t1.0
Top2       (0, 7165)\t1.0\n  (1, 18347)\t1.0\n  (2, 39317)\t1.0\n  (3, 21040)\t1.0\n  (4, 15613)\t1.0\n  (5, 22769)\t1.0
Top3       (0, 7165)\t1.0\n  (1, 18347)\t1.0\n  (2, 39317)\t1.0\n  (3, 21040)\t1.0\n  (4, 15613)\t1.0\n  (5, 22769)\t1.0
Top4       (0, 7165)\t1.0\n  (1, 18347)\t1.0\n  (2, 39317)\t1.0\n  (3, 21040)\t1.0\n  (4, 15613)\t1.0\n  (5, 22769)\t1.0
Top5       (0, 7165)\t1.0\n  (1, 18347)\t1.0\n  (2, 39317)\t1.0\n  (3, 21040)\t1.0\n  (4, 15613)\t1.0\n  (5, 22769)\t1.0
                                                              ...                                                       
Top21      (0, 7165)\t1.0\n  (1, 18347)\t1.0\n  (2, 39317)\t1.0\n  (3, 21040)\t1.0\n  (4, 15613)\t1.0\n  (5, 22769)\t1.0
Top22      (0, 7165)\t1.0\n  (1, 18347)\t1.0\n  (2, 39317)\t1.0\n  (3, 21040)\t1.0\n  (4, 15613)\t1.0\n  (5, 22769)\t1.0
Top23      (0, 7165)\t1.0\n  (1,

Top1       (0, 36160)\t1.0\n  (1, 19560)\t1.0\n  (2, 35310)\t1.0\n  (3, 13229)\t1.0\n  (4, 4332)\t1.0\n  (5, 7034)\t1.0\n  (6, 8451)\t1.0\n  (7, 20421)\t1.0\n  (8, 14218)\t1.0\n  (9, 22221)\t1.0\n  (10, 7402)\t1.0\n  (11, 35707)\t1.0
Top2       (0, 36160)\t1.0\n  (1, 19560)\t1.0\n  (2, 35310)\t1.0\n  (3, 13229)\t1.0\n  (4, 4332)\t1.0\n  (5, 7034)\t1.0\n  (6, 8451)\t1.0\n  (7, 20421)\t1.0\n  (8, 14218)\t1.0\n  (9, 22221)\t1.0\n  (10, 7402)\t1.0\n  (11, 35707)\t1.0
Top3       (0, 36160)\t1.0\n  (1, 19560)\t1.0\n  (2, 35310)\t1.0\n  (3, 13229)\t1.0\n  (4, 4332)\t1.0\n  (5, 7034)\t1.0\n  (6, 8451)\t1.0\n  (7, 20421)\t1.0\n  (8, 14218)\t1.0\n  (9, 22221)\t1.0\n  (10, 7402)\t1.0\n  (11, 35707)\t1.0
Top4       (0, 36160)\t1.0\n  (1, 19560)\t1.0\n  (2, 35310)\t1.0\n  (3, 13229)\t1.0\n  (4, 4332)\t1.0\n  (5, 7034)\t1.0\n  (6, 8451)\t1.0\n  (7, 20421)\t1.0\n  (8, 14218)\t1.0\n  (9, 22221)\t1.0\n  (10, 7402)\t1.0\n  (11, 35707)\t1.0
Top5       (0, 36160)\t1.0\n  (1, 19560)\t1.0\n  (2, 35310)\t1.0

...

Name: 1871, Length: 25, dtype: object
Top1     [china, participate, sanctions, nkorea]                                                 
Top2     [aiming, ban, child, marriages, shot, pakistan, antiislamic, blasphemous]               
Top3     [tsai, ingwen, elected, taiwans, female, president]                                     
Top4     [schoolgirls, report, abuse, young, asylum, seekers]                                    
Top5     [prisoners, freed, iran, prisoners, include, washington, post, reporter, jason, rezaian]
                                                   ...                                           
Top21    [facebook, outsources, fight, racist, posts, germany]                                   
Top22    [gunfire, explosions, heard, burkina, faso, hotel]                                      
Top23    [burkina, faso, security, forces, raid, besieged, hotel, free, hostages]                
Top24    [julian, assange, questioned, swedish, prosecutors, london]            

Top1     [china, bans, depictions, gay, people, adultery, night, stands, cleavage, reincarnation, television]                                                                                                                                                         
Top2     [peanut, allergy, risk, reduced, 80, consuming, peanuts, infant, research, suggests]                                                                                                                                                                         
Top3     [philippines, seizes, north, korean, ship]                                                                                                                                                                                                                   
Top4     [refugee, children, calais, jungle, camp, raped, aid, workers, claim]                                                                                                                                     

Top1     [wildfire, destroying, fort, mcmurray, city, evacuated]                                                                                                                                  
Top2     [selfproclaimed, sharia, police, germany, stand, trial, grounds, violating, laws, wearing, uniforms, political, messages]                                                                
Top3     [doubts, rise, ttip, france, threatens, block, euus, deal]                                                                                                                               
Top4     [seven, worlds, biggest, banks, agreed, pay, 324, million, settle, private, lawsuit, accusing, rigging, rate, benchmark, used, 553, trillion, derivatives, market]                       
Top5     [jewish, man, handed, life, prison, grisly, murder, east, jerusalem, teen, israeli, ringleader, killing, palestinian, teenager, abducted, burned, death, 2014, sentenced, life, prison]  
                         

Top1     [jamaica, proposes, marijuana, dispensers, tourists, airports, following, legalisation, kiosks, desks, people, license, purchase, ounces, drug, use, stay]                                                              
Top2     [stephen, hawking, says, pollution, stupidity, biggest, threats, mankind, certainly, greedy, stupid, treatment, environment, past, decade]                                                                              
Top3     [boris, johnson, says, run, tory, party, leadership]                                                                                                                                                                    
Top4     [gay, men, ivory, coast, abused, forced, flee, homes, pictured, signing, condolence, book, victims, recent, attack, gay, nightclub, florida]                                                                            
Top5     [switzerland, denies, citizenship, muslim, immigrant, girls, refused, swim, boys, repor

IndexError: single positional indexer is out-of-bounds

In [32]:
from sklearn.feature_extraction.text import CountVectorizer
vectorizer = CountVectorizer(
    analyzer = 'word',
    strip_accents = 'unicode',
    lowercase = True,
    stop_words = sw,
)

From sklearn, create a CountVectorizer, a class of methods that vectorizes text data into counts of their words, letters, etc. In this instance, the CountVectorizer calcuates word frequencies via the analyzer parameter.

# Begin training
Using cross cross validation methods, create a train_test_split, fit the training sets to a logistic classifier model, and interpret the accuracy.

In [61]:
from sklearn.cross_validation import train_test_split
X_train, X_test, y_train, y_test = train_test_split(
    features,
    data_labels,
    train_size = 0.80,
    random_state = 1234
)

ValueError: Found input variables with inconsistent numbers of samples: [553377, 1986]

Create a training set via the CrossValidation library in sklearn. 

In [58]:
from sklearn.linear_model import LogisticRegression
log_model = LogisticRegression()

Create a logistic regresssion classifier object.

In [59]:
log_model = log_model.fit(X=X_train, y=y_train)
y_pred = log_model.predict(X_test)

Produce a log model that can be trained on the X_train partition of the dataset and the y_train partition of the dataset. Then produce an array of predicted labels correponding to the X_test dataset partition.

# Baseline result (logistic regression)

In [60]:
from sklearn.metrics import accuracy_score
print(make_percent(accuracy_score(y_test, y_pred)))


45.73%


The resulting accuracy of the classifer.

Remember, this accuracy is from using the top headline for each day, not taking into consideration the other 24 headlines. Lets try to use some different classification algorithms and compare results.

# Different classifiers
We will try Naive Bayes, Decision tree (gini criteria), KNN, and some ensemble methods.

## Naive Bayes

In [ ]:
from sklearn.naive_bayes import GaussianNB
gnbc = GaussianNB()
gnbc.fit(X_train.toarray(), y_train)
print(make_percent(gnbc.score(X_test.toarray(), y_test)))

Accuracy is even worse! That's ok, differnt classifiers - different results. Lets try a decision tree next.

## Decision Tree (Gini)

In [ ]:
from sklearn.tree import DecisionTreeClassifier